In [13]:
pip install spectral

Note: you may need to restart the kernel to use updated packages.


In [ ]:
cp base.py /opt/conda/envs/macrosystems/lib/python3.10/site-packages/hytools/base.py


In [ ]:
GOCMD_VER=$(curl -L -s https://raw.githubusercontent.com/cyverse/gocommands/main/VERSION.txt); \
curl -L -s https://github.com/cyverse/gocommands/releases/download/${GOCMD_VER}/gocmd-${GOCMD_VER}-linux-amd64.tar.gz | tar zxvf -

In [ ]:
./gocmd put --diff --icat --retry 3 -d -k  cross-sensor-cal/YELL_2023_07 i:/iplant/home/shared/earthlab/macrosystems/processed_flight_lines > debug_log.txt 2>&1

In [15]:
import hytools as ht
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import random
import nbconvert
import time
import re

### Loading Earth Lab Spectral Tools

# 1. Enable autoreload in your Jupyter Notebook:

%load_ext autoreload
%autoreload 2

# 2. Import the custom tools module:

import spectral_unmixing_tools_original as el_spectral

# 3. Verify that the tools loaded correctly by printing the module's directory:

print(dir(el_spectral))

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
['CRS', 'ENVIProcessor', 'GradientBoostingRegressor', 'Resampling', '__builtins__', '__cached__', '__doc__', '__file__', '__loader__', '__name__', '__package__', '__spec__', 'apply_topo_and_brdf_corrections', 'boosted_quantile_plot', 'boosted_quantile_plot_by_sensor', 'box', 'calculate_default_transform', 'clean_csv_files_in_subfolders', 'clean_data_and_write_to_csv', 'concatenate_sensors', 'control_function', 'control_function_for_extraction', 'download_neon_file', 'download_neon_flight_lines', 'extract_overlapping_layers_to_2d_dataframe', 'find_raster_files', 'find_raster_files_for_extraction', 'fit_models_with_different_alpha', 'flight_lines_to_envi', 'generate_config_json', 'generate_correction_configs', 'generate_correction_configs_for_directory', 'get_crs_from_hdr', 'get_spectral_data_and_wavelengths', 'glob', 'go_forth_and_multiply', 'gpd', 'h5py', 'ht', 'jefe', 'json', 'load_and_combine_rast

In [51]:
# NIWO - 2020-07
base_folder = 'next_test'
site_code = 'NIWO'
product_code = 'DP1.30006.001'
year_month = '2020-08'
flight_lines = [
    'NEON_D13_NIWO_DP1_20200731_155646_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)


Processing flight line: NEON_D13_NIWO_DP1_20200731_155646_reflectance
Data retrieved successfully for 2020-08!
Download completed for NEON_D13_NIWO_DP1_20200731_155646_reflectance.h5
Download completed.

Processing: ./NEON_D13_NIWO_DP1_20200731_155646_reflectance.h5
Command executed successfully
Standard Output: Here we GO!
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTools pid=108090) R
(HyTools pid=108090) G
(HyTool

Processing subdirectories:   0%|          | 0/1 [00:00<?, ?directory/s]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   0%|          | 0/93 [00:00<?, ?chunk/s]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   1%|          | 1/93 [00:14<22:55, 14.95s/chunk]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   2%|▏         | 2/93 [00:29<22:42, 14.97s/chunk]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   3%|▎         | 3/93 [00:45<22:35, 15.06s/chunk]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   4%|▍         | 4/93 [01:00<22:20, 15.06s/chunk]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   5%|▌         | 5/93 [01:15<22:06, 15.08s/chunk]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   6%|▋         | 6/93 [01:30<21:59, 15.17s/chunk]
Processing NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked:   8%|▊         | 7/93 [01:45<21:42, 15.14s/chunk]
Processing NEON_

KeyboardInterrupt: 

In [46]:
import os
import glob
def find_raster_files(directory):
    """
    Debug version: Logs all files before filtering to ensure they are being read correctly.
    """
    pattern = os.path.join(directory, '*')
    all_files = glob.glob(pattern)

    # Debugging: Print all files
    print(f"All files in {directory}:")
    for file in all_files:
        print(f"  {file}")

    filtered_files = [
        file for file in all_files
        if (
            ('_reflectance' in os.path.basename(file) or
             '_envi' in os.path.basename(file) or
             file.endswith('.img')) and
            not file.endswith('.json') and
            not file.endswith('.hdr') and
            '_mask' not in file and
            '_ancillary' not in file
        )
    ]

    # Debugging: Print filtered files
    print(f"Filtered files in {directory}:")
    for file in filtered_files:
        print(f"  {file}")

    return filtered_files

el_spectral.find_raster_files('next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance')


['next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance',
 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi',
 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_resample_Landsat_5_TM.img',
 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_resample_Landsat_7_ETMplus.img',
 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_resample_Landsat_8_OLI.img',
 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_resample_Landsat_9_OLI-2.img',
 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_resample_MicaSense.img',
 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_1

In [12]:
base_folder = '/home/jovyan/data-store/home/shared/earthlab/macrosystems/cross-sensor-cal/sorted_files/envi/Reflectance__ENVI_Masked'
polygon_layer = "aop_macrosystems_data_1_7_25.geojson"
    
el_spectral.process_base_folder(
    base_folder=base_folder,
    polygon_layer=polygon_layer,
    raster_crs_override="EPSG:4326",  # Optional CRS override
    polygons_crs_override="EPSG:4326",  # Optional CRS override
    output_masked_suffix="_masked",  # Optional suffix for output
    plot_output=False,  # Disable plotting
    dpi=300  # Set plot resolution
)

Found 0 subdirectories in /home/jovyan/data-store/home/shared/earthlab/macrosystems/cross-sensor-cal/sorted_files/envi/Reflectance__ENVI_Masked.

All subdirectories processed.


In [11]:
import os

print(os.getcwd())

/home/jovyan/data-store/cross-sensor-cal


In [23]:
base_folder = 'table_mountain'
site_code = 'CPER'
product_code = 'DP1.30006.001'
year_month = '2021-09'
flight_lines = [
    'NEON_D10_R10C_DP1_20210915_191104',
    'NEON_D10_R10C_DP1_20210915_191530',
    'NEON_D10_R10C_DP1_20210915_192104',
    'NEON_D10_R10C_DP1_20210915_192523',
    'NEON_D10_R10C_DP1_20210915_193014',
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)


Processing flight line: NEON_D10_R10C_DP1_20210915_191104
Data retrieved successfully for 2021-09!
Flight line NEON_D10_R10C_DP1_20210915_191104 not found in the data for 2021-09.
Download completed.

Processing flight line: NEON_D10_R10C_DP1_20210915_191530
Data retrieved successfully for 2021-09!
Flight line NEON_D10_R10C_DP1_20210915_191530 not found in the data for 2021-09.
Download completed.

Processing flight line: NEON_D10_R10C_DP1_20210915_192104
Data retrieved successfully for 2021-09!
Flight line NEON_D10_R10C_DP1_20210915_192104 not found in the data for 2021-09.
Download completed.

Processing flight line: NEON_D10_R10C_DP1_20210915_192523
Data retrieved successfully for 2021-09!
Flight line NEON_D10_R10C_DP1_20210915_192523 not found in the data for 2021-09.
Download completed.

Processing flight line: NEON_D10_R10C_DP1_20210915_193014
Data retrieved successfully for 2021-09!
Flight line NEON_D10_R10C_DP1_20210915_193014 not found in the data for 2021-09.
Download complet

Processing subdirectories: 0directory [00:00, ?directory/s]

Jefe finished. Please check for the _with_mask_and_all_spectra.csv for your  hyperspectral data from NEON flight lines extracted to match your provided polygons


In [11]:
# Define inputs for 2023-07
base_folder = 'NIWO_2023_07'
site_code = 'NIWO'
product_code = 'DP1.30006.001'
year_month = '2023-07'
flight_lines = [
    'NEON_D13_NIWO_DP1_L003-1_20230724_directional_reflectance'
]

# Call the function for July 2023
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)

base_folder = 'NIWO_2023_08'
# Define inputs for 2023-08
year_month = '2023-08'
flight_lines = [
    'NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance',
    'NEON_D13_NIWO_DP1_L003-1_20230815_directional_reflectance',
    'NEON_D13_NIWO_DP1_L004-1_20230815_directional_reflectance',
    'NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance',
    'NEON_D13_NIWO_DP1_L011-1_20230815_directional_reflectance',
    'NEON_D13_NIWO_DP1_L012-1_20230815_directional_reflectance',
    'NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance',
    'NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance'
]

# Call the function for August 2023
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)


Processing flight line: NEON_D13_NIWO_DP1_L003-1_20230724_directional_reflectance
Data retrieved successfully for 2023-07!
Flight line NEON_D13_NIWO_DP1_L003-1_20230724_directional_reflectance not found in the data for 2023-07.
Download completed.

Processing: ./NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance.h5
Command executed successfully
Standard Output: Here we GO!
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(HyTools pid=31319) G
(HyTools pid=31319) R
(

Processing subdirectories:   0%|          | 0/2 [00:00<?, ?directory/s]

[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_ancillary: Must pass either crs or epsg.
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi_mask: name 're' is not defined
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L

Processing subdirectories:  50%|█████     | 1/2 [00:28<00:28, 28.14s/directory]

[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img: name 're' is not defined
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L003-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L003-1_20230815_directional_reflectance_masked: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L003-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L003-1_20230815_directional_reflectance_ancillary: Must pass either crs or epsg.
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L003-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L003-1_20230815_directional_reflectance__envi: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_07/NEON_D13_NIWO_DP1_L003-1_2023

...

[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L012-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L012-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img: name 're' is not defined
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance_masked: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance_ancillary: Must pass either crs or epsg.
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance__envi: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L017-1_2023

Processing subdirectories:  88%|████████▊ | 7/8 [03:21<00:28, 28.78s/directory]

[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L017-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img: name 're' is not defined
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance_masked: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance_ancillary: Must pass either crs or epsg.
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance__envi: Unexpected number of files with 426 bands.
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L018-1_2023

Processing subdirectories: 100%|██████████| 8/8 [03:50<00:00, 28.86s/directory]

[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L018-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img: name 're' is not defined
Jefe finished. Please check for the _with_mask_and_all_spectra.csv for your  hyperspectral data from NEON flight lines extracted to match your provided polygons


In [ ]:

base_folder = 'NIWO_2023_08'
polygon_layer = "aop_macrosystems_data_1_7_25.geojson"

el_spectral.process_all_subdirectories(base_folder, polygon_layer)

Processing subdirectories:   0%|          | 0/8 [00:00<?, ?directory/s]

[ERROR] Could not extract CRS from NIWO_2023_08/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked: 'utf-8' codec can't decode byte 0x80 in position 4: invalid start byte
[INFO] Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked as Masked_band_
[INFO] Processing raster: NIWO_2023_08/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked with 426 bands.



Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   0%|          | 0/146 [00:00<?, ?chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   1%|          | 1/146 [00:00<01:59,  1.22chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   1%|▏         | 2/146 [00:01<01:19,  1.81chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   2%|▏         | 3/146 [00:01<01:07,  2.12chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   3%|▎         | 4/146 [00:01<01:01,  2.31chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   3%|▎         | 5/146 [00:02<01:00,  2.35chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   4%|▍         | 6/146 [00:02<00:57,  2.46chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_masked:   5%|▍         | 7/146 [00:03<00:5

[ERROR] Could not extract CRS from NIWO_2023_08/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_ancillary: 'utf-8' codec can't decode byte 0xc6 in position 3: invalid continuation byte
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance_ancillary: Must pass either crs or epsg.
[ERROR] Could not extract CRS from NIWO_2023_08/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi: 'utf-8' codec can't decode byte 0xc6 in position 3: invalid continuation byte
[INFO] Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi as ENVI_band_
[INFO] Processing raster: NIWO_2023_08/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi with 426 bands.



Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   0%|          | 0/146 [00:00<?, ?chunk/s]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   1%|          | 1/146 [00:09<23:12,  9.60s/chunk]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   1%|▏         | 2/146 [00:20<25:07, 10.47s/chunk]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   2%|▏         | 3/146 [00:31<25:37, 10.75s/chunk]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   3%|▎         | 4/146 [00:41<24:54, 10.52s/chunk]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   3%|▎         | 5/146 [00:52<24:29, 10.42s/chunk]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   4%|▍         | 6/146 [01:01<23:46, 10.19s/chunk]
Processing NEON_D13_NIWO_DP1_L019-1_20230815_directional_reflectance__envi:   5%|▍         | 7/146 [01:12<23:48, 10.28

...


Processing NEON_D13_NIWO_DP1_L004-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img:   0%|          | 0/132 [00:00<?, ?chunk/s]
Processing NEON_D13_NIWO_DP1_L004-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img:   8%|▊         | 11/132 [00:00<00:01, 106.36chunk/s]
Processing NEON_D13_NIWO_DP1_L004-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img:  17%|█▋        | 23/132 [00:00<00:00, 112.30chunk/s]
Processing NEON_D13_NIWO_DP1_L004-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img:  27%|██▋       | 35/132 [00:00<00:01, 94.89chunk/s] 
Processing NEON_D13_NIWO_DP1_L004-1_20230815_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked.img:  34%|███▍      | 45/132 [00:00<00:01, 54.13chunk/s]
Processing NEON_D13_NIWO_DP1_L004-1_20230815_directional_reflectance__envi_resample_MicaSense-to-mat

[ERROR] Could not extract CRS from NIWO_2023_08/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked: 'utf-8' codec can't decode byte 0x80 in position 4: invalid start byte
[INFO] Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked as Masked_band_
[INFO] Processing raster: NIWO_2023_08/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked with 426 bands.



Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   0%|          | 0/120 [00:00<?, ?chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   1%|          | 1/120 [00:00<01:43,  1.15chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   2%|▏         | 2/120 [00:01<01:07,  1.76chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   2%|▎         | 3/120 [00:01<00:54,  2.16chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   3%|▎         | 4/120 [00:01<00:50,  2.28chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   4%|▍         | 5/120 [00:02<00:48,  2.37chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   5%|▌         | 6/120 [00:02<00:46,  2.44chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_masked:   6%|▌         | 7/120 [00:03<00:4

[ERROR] Could not extract CRS from NIWO_2023_08/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_ancillary: 'utf-8' codec can't decode byte 0xc6 in position 3: invalid continuation byte
[ERROR] Error while processing raster file NIWO_2023_08/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance_ancillary: Must pass either crs or epsg.
[ERROR] Could not extract CRS from NIWO_2023_08/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi: 'utf-8' codec can't decode byte 0xc6 in position 3: invalid continuation byte
[INFO] Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi as ENVI_band_
[INFO] Processing raster: NIWO_2023_08/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance/NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi with 426 bands.



Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   0%|          | 0/120 [00:00<?, ?chunk/s]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   1%|          | 1/120 [00:05<11:06,  5.60s/chunk]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   2%|▏         | 2/120 [00:14<14:50,  7.55s/chunk]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   2%|▎         | 3/120 [00:23<16:06,  8.26s/chunk]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   3%|▎         | 4/120 [00:32<16:43,  8.65s/chunk]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   4%|▍         | 5/120 [00:42<17:22,  9.07s/chunk]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   5%|▌         | 6/120 [00:52<17:34,  9.25s/chunk]
Processing NEON_D13_NIWO_DP1_L010-1_20230815_directional_reflectance__envi:   6%|▌         | 7/120 [01:02<17:58,  9.54

In [33]:
import pandas as pd

# Path to the cleaned CSV file
original_csv_label = 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance_masked_spectral_data.csv'
corrected_csv_label = "next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_masked_spectral_data.csv"
resampled_label = 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2_masked_spectral_data.csv'
resampled_label_2 = 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_resample_Landsat_8_OLI_masked_spectral_data.csv'
merged_output = 'next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/merged_output.csv'
# Load the first few rows of the cleaned CSV file
df_preview = pd.read_csv(merged_output, nrows=5)

# Display all columns in the preview
pd.set_option('display.max_columns', None)  # Show all columns
print(df_preview)

   Polygon_ID                              GlobalID  \
0         0.0  6d0b0003-0760-4c5e-83f0-58705eda9b22   
1         0.0  6d0b0003-0760-4c5e-83f0-58705eda9b22   
2         0.0  6d0b0003-0760-4c5e-83f0-58705eda9b22   
3         0.0  6d0b0003-0760-4c5e-83f0-58705eda9b22   
4      1284.0  cce70ec2-68f9-4096-8567-e2f6a98e3fd3   

                    CreationDate                     Creator  \
0  Tue, 06 Jun 2023 16:11:20 GMT  Tyler.L.McIntosh_ucboulder   
1  Tue, 06 Jun 2023 16:11:20 GMT  Tyler.L.McIntosh_ucboulder   
2  Tue, 06 Jun 2023 16:11:20 GMT  Tyler.L.McIntosh_ucboulder   
3  Tue, 06 Jun 2023 16:11:20 GMT  Tyler.L.McIntosh_ucboulder   
4  Wed, 21 Jun 2023 15:23:08 GMT  Tyler.L.McIntosh_ucboulder   

                        EditDate                      Editor  \
0  Tue, 06 Jun 2023 16:11:20 GMT  Tyler.L.McIntosh_ucboulder   
1  Tue, 06 Jun 2023 16:11:20 GMT  Tyler.L.McIntosh_ucboulder   
2  Tue, 06 Jun 2023 16:11:20 GMT  Tyler.L.McIntosh_ucboulder   
3  Tue, 06 Jun 2023 16:11:20

In [32]:
import os
import pandas as pd

import os
import pandas as pd

import os
import pandas as pd

def merge_csvs_by_columns(base_folder):
    """
    Merges all CSV files in each subdirectory of the given base folder by columns,
    ensuring that metadata columns on the left are included only once.

    Args:
        base_folder (str): Path to the base folder containing subdirectories with CSV files.
    """
    # List all subdirectories in the base folder
    subdirectories = [
        os.path.join(base_folder, sub_dir)
        for sub_dir in os.listdir(base_folder)
        if os.path.isdir(os.path.join(base_folder, sub_dir))
    ]

    for subdirectory in subdirectories:
        print(f"[INFO] Processing subdirectory: {subdirectory}")
        
        # Extract the flight line name from the subdirectory name
        flight_line_name = os.path.basename(subdirectory)

        # Find all CSV files in the subdirectory
        csv_files = [
            os.path.join(subdirectory, file)
            for file in os.listdir(subdirectory)
            if file.endswith(".csv")
        ]

        if not csv_files:
            print(f"[INFO] No CSV files found in {subdirectory}. Skipping.")
            continue

        # Read all CSV files
        dataframes = [pd.read_csv(csv) for csv in csv_files]

        # Separate metadata columns from spectral columns
        metadata_columns = dataframes[0].columns.tolist()
        for df in dataframes[1:]:
            metadata_columns = [
                col for col in metadata_columns if col in df.columns
            ]
        
        # Merge files column-wise
        merged_df = dataframes[0]  # Start with the first DataFrame
        for df in dataframes[1:]:
            # Exclude metadata columns from subsequent files
            spectral_columns = [col for col in df.columns if col not in metadata_columns]
            df = df[spectral_columns]
            merged_df = pd.concat([merged_df, df], axis=1)

        # Generate the output file name
        output_csv_name = f"{flight_line_name}_with_mask_and_all_spectra.csv"
        output_csv_path = os.path.join(subdirectory, output_csv_name)

        # Save the merged CSV
        merged_df.to_csv(output_csv_path, index=False)
        print(f"[INFO] Merged CSV saved to: {output_csv_path}")

    print("[INFO] Processing complete for all subdirectories.")

base_folder = 'next_test'
merge_csvs_by_columns(base_folder)



[INFO] Processing subdirectory: next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance
[INFO] Merged CSV saved to: next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance_with_mask_and_all_spectra.csv
[INFO] Processing complete for all subdirectories.


In [24]:
el_spectral.merge_csvs_by_columns(base_folder)

[INFO] Processing subdirectory: next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance
[INFO] Merged CSV saved to: next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/polygon_merged_output.csv
[INFO] Processing complete for all subdirectories.


In [9]:
 polygon_layer = "aop_macrosystems_data_1_7_25.geojson"
el_spectral.process_base_folder(
    base_folder=base_folder,
    polygon_layer=polygon_layer,
    raster_crs_override="EPSG:4326",  # Optional CRS override
    polygons_crs_override="EPSG:4326",  # Optional CRS override
    output_masked_suffix="_masked",  # Optional suffix for output
    plot_output=False,  # Disable plotting
    dpi=300  # Set plot resolution
    )

Found 4 subdirectories in non_provisional_flightlines_NIWO.

Processing subdirectory: non_provisional_flightlines_NIWO/NEON_D13_NIWO_DP1_20200731_153721_reflectance
Found 20 ENVI raster files in non_provisional_flightlines_NIWO/NEON_D13_NIWO_DP1_20200731_153721_reflectance.

Processing ENVI file: non_provisional_flightlines_NIWO/NEON_D13_NIWO_DP1_20200731_153721_reflectance/NEON_D13_NIWO_DP1_20200731_153721_reflectance
Raster CRS: EPSG:32613
Polygons CRS: EPSG:4326
Reprojecting polygons to match raster CRS...
Reprojection complete.
Clipping polygons to raster bounds...
Number of Clipped Polygons: 294
Clipped Polygons Bounds: [ 457845.         4428624.96455012  458049.26777551 4434268.09674941]
Raster has a valid geotransform.
Creating mask from polygons...
Mask created with shape (10494, 905). Inside pixels: 10844
Unique values in mask: [False  True]
Using nodata value: -9999.0
Masked data shape: (426, 10494, 905)
Masked raster saved to: non_provisional_flightlines_NIWO/NEON_D13_NIWO_D

In [ ]:

# WREF - 2023-06 (Part 1)
base_folder = 'WREF_weedend_run'
site_code = 'WREF'
product_code = 'DP1.30006.001'
year_month = '2023-06'
flight_lines = [
    'NEON_D16_WREF_DP1_L001-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L001-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L019-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L020-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L021-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L023-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L024-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L028-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L029-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L031-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L032-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L033-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L036-1_20230624_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)


Processing flight line: NEON_D16_WREF_DP1_L001-1_20230625_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L001-1_20230625_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L001-1_20230630_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L001-1_20230630_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L019-1_20230625_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L019-1_20230625_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L020-1_20230625_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L020-1_20230625_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L021-1_20230625_directional_reflectance
Data r

In [ ]:
# NIWO - 2020-07
base_folder = 'non_provisional_flightlines_NIWO'
site_code = 'NIWO'
product_code = 'DP1.30006.001'
year_month = '2020-07'
flight_lines = [
    'NEON_D13_NIWO_DP1_20200731_151902_reflectance',
    'NEON_D13_NIWO_DP1_20200731_153721_reflectance',
    'NEON_D13_NIWO_DP1_20200731_154336_reflectance',
    'NEON_D13_NIWO_DP1_20200731_155024_reflectance',
    'NEON_D13_NIWO_DP1_20200731_155646_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)

# NIWO - 2020-08
base_folder = 'non_provisional_flightlines_NIWO'
site_code = 'NIWO'
product_code = 'DP1.30006.001'
year_month = '2020-08'
flight_lines = [
    'NEON_D13_NIWO_DP1_20200801_152930_reflectance',
    'NEON_D13_NIWO_DP1_20200801_160814_reflectance',
    'NEON_D13_NIWO_DP1_20200801_161441_reflectance',
    'NEON_D13_NIWO_DP1_20200801_162052_reflectance',
    'NEON_D13_NIWO_DP1_20200801_162711_reflectance',
    'NEON_D13_NIWO_DP1_20200801_163340_reflectance',
    'NEON_D13_NIWO_DP1_20200807_160712_reflectance',
    'NEON_D13_NIWO_DP1_20200807_163444_reflectance',
    'NEON_D13_NIWO_DP1_20200807_164808_reflectance',
    'NEON_D13_NIWO_DP1_20200807_165500_reflectance',
    'NEON_D13_NIWO_DP1_20200807_154502_reflectance',
    'NEON_D13_NIWO_DP1_20200807_155314_reflectance',
    'NEON_D13_NIWO_DP1_20200807_160118_reflectance',
    'NEON_D13_NIWO_DP1_20200807_161351_reflectance',
    'NEON_D13_NIWO_DP1_20200807_162134_reflectance',
    'NEON_D13_NIWO_DP1_20200807_162829_reflectance',
    'NEON_D13_NIWO_DP1_20200807_164154_reflectance',
    'NEON_D13_NIWO_DP1_20200807_172100_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)
# WREF - 2023-06 (Part 2)
base_folder = 'non_provisional_flightlines_WREF'
site_code = 'WREF'
product_code = 'DP1.30006.001'
year_month = '2023-06'
flight_lines = [
    'NEON_D16_WREF_DP1_L040-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L041-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L042-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L043-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L046-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L051-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L053-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L054-2_20230628_directional_reflectance',
    'NEON_D16_WREF_DP1_L055-1_20230628_directional_reflectance',
    'NEON_D16_WREF_DP1_L062-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L063-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L064-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L065-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L067-1_20230630_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)


# WREF - 2023-06
base_folder = 'non_provisional_flightlines_WREF'
site_code = 'WREF'
product_code = 'DP1.30006.001'
year_month = '2023-06'
flight_lines = [
    'NEON_D16_WREF_DP1_L001-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L001-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L019-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L020-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L021-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L023-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L024-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L028-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L029-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L031-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L032-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L033-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L036-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L040-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L041-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L042-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L043-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L046-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L051-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L053-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L054-2_20230628_directional_reflectance',
    'NEON_D16_WREF_DP1_L055-1_20230628_directional_reflectance',
    'NEON_D16_WREF_DP1_L062-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L063-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L064-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L065-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L067-1_20230630_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)

# YELL - 2023-07
base_folder = 'non_provisional_flightlines_YELL'
site_code = 'YELL'
product_code = 'DP1.30006.001'
year_month = '2023-07'
flight_lines = [
    'NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance',
    'NEON_D12_YELL_DP1_L001-1_20230719_directional_reflectance',
    'NEON_D12_YELL_DP1_L007-1_20230718_directional_reflectance',
    'NEON_D12_YELL_DP1_L011-1_20230718_directional_reflectance',
    'NEON_D12_YELL_DP1_L013-1_20230718_directional_reflectance',
    'NEON_D12_YELL_DP1_L014-1_20230718_directional_reflectance',
    'NEON_D12_YELL_DP1_L024-1_20230718_directional_reflectance',
    'NEON_D12_YELL_DP1_L024-1_20230719_directional_reflectance',
    'NEON_D12_YELL_DP1_L025-1_20230719_directional_reflectance',
    'NEON_D12_YELL_DP1_L029-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L031-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L032-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L033-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L036-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L037-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L038-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L040-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L046-1_20230703_directional_reflectance',
    'NEON_D12_YELL_DP1_L050-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L051-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L065-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L067-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L073-1_20230719_directional_reflectance',
    'NEON_D12_YELL_DP1_L074-1_20230718_directional_reflectance',
    'NEON_D12_YELL_DP1_L075-1_20230718_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)


In [ ]:
# WREF - 2023-06 (Part 1)
base_folder = 'non_provisional_flightlines_WREF'
site_code = 'WREF'
product_code = 'DP1.30006.001'
year_month = '2023-06'
flight_lines = [
    'NEON_D16_WREF_DP1_L001-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L001-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L019-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L020-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L021-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L023-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L024-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L028-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L029-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L031-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L032-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L033-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L036-1_20230624_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)




In [ ]:
# WREF - 2023-06 (Part 2)
base_folder = 'WREF_2023_6'
site_code = 'WREF'
product_code = 'DP1.30006.001'
year_month = '2023-06'
flight_lines = [
    'NEON_D16_WREF_DP1_L040-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L041-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L042-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L043-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L046-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L051-1_20230624_directional_reflectance',
    'NEON_D16_WREF_DP1_L053-1_20230625_directional_reflectance',
    'NEON_D16_WREF_DP1_L054-2_20230628_directional_reflectance',
    'NEON_D16_WREF_DP1_L055-1_20230628_directional_reflectance',
    'NEON_D16_WREF_DP1_L062-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L063-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L064-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L065-1_20230630_directional_reflectance',
    'NEON_D16_WREF_DP1_L067-1_20230630_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)




Processing flight line: NEON_D16_WREF_DP1_L040-1_20230625_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L040-1_20230625_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L041-1_20230625_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L041-1_20230625_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L042-1_20230625_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L042-1_20230625_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L043-1_20230625_directional_reflectance
Data retrieved successfully for 2023-06!
Download completed for NEON_D16_WREF_DP1_L043-1_20230625_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D16_WREF_DP1_L046-1_20230624_directional_reflectance
Data r

In [7]:
# YELL - 2023-07 (Part 1)
base_folder = 'YELL_2023_07_C'
site_code = 'YELL'
product_code = 'DP1.30006.001'
year_month = '2023-07'
flight_lines = [
    'NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance'#,
    #'NEON_D12_YELL_DP1_L001-1_20230719_directional_reflectance',
    #'NEON_D12_YELL_DP1_L007-1_20230718_directional_reflectance',
    #'NEON_D12_YELL_DP1_L011-1_20230718_directional_reflectance',
    #'NEON_D12_YELL_DP1_L013-1_20230718_directional_reflectance',
    #'NEON_D12_YELL_DP1_L014-1_20230718_directional_reflectance',
    #'NEON_D12_YELL_DP1_L024-1_20230718_directional_reflectance',
    #'NEON_D12_YELL_DP1_L024-1_20230719_directional_reflectance',
    #'NEON_D12_YELL_DP1_L025-1_20230719_directional_reflectance',
    #'NEON_D12_YELL_DP1_L029-1_20230715_directional_reflectance',
    #'NEON_D12_YELL_DP1_L031-1_20230715_directional_reflectance',
    #'NEON_D12_YELL_DP1_L032-1_20230715_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)



Processing flight line: NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance
Data retrieved successfully for 2023-07!
Download completed for NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance.h5
Download completed.

Processing: ./NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance.h5
Command executed successfully
Standard Output: Here we GO!
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=126236) R
(HyTools pid=126236) G
(HyTools pid=1262

Processing subdirectories:   0%|          | 0/1 [00:00<?, ?directory/s]

[ERROR] Could not extract CRS from YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance: 'utf-8' codec can't decode byte 0xf1 in position 0: invalid continuation byte
[INFO] Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance as Original_band_
[INFO] Processing raster: YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance with 426 bands.



Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:   0%|          | 0/34 [00:00<?, ?chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:   3%|▎         | 1/34 [00:00<00:09,  3.42chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:   6%|▌         | 2/34 [00:00<00:12,  2.49chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:   9%|▉         | 3/34 [00:01<00:14,  2.14chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:  12%|█▏        | 4/34 [00:01<00:16,  1.86chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:  15%|█▍        | 5/34 [00:02<00:17,  1.69chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:  18%|█▊        | 6/34 [00:03<00:19,  1.45chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance:  21%|██        | 7/34 [00:04<00:22,  1.18chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_di

[ERROR] Could not extract CRS from YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance_ancillary: 'utf-8' codec can't decode byte 0xc6 in position 3: invalid continuation byte
[ERROR] Error while processing raster file YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance_ancillary: Must pass either crs or epsg.
[ERROR] Could not extract CRS from YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi: 'utf-8' codec can't decode byte 0xc6 in position 3: invalid continuation byte
[INFO] Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi as ENVI_band_
[INFO] Processing raster: YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi with 426 bands.


...

[INFO] Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img as ENVI_band_
[INFO] Processing raster: YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img with 4 bands.



Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img:   0%|          | 0/34 [00:00<?, ?chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img:   6%|▌         | 2/34 [00:00<00:02, 11.34chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img:  12%|█▏        | 4/34 [00:00<00:03,  8.29chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img:  15%|█▍        | 5/34 [00:00<00:03,  7.36chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img:  18%|█▊        | 6/34 [00:00<00:04,  6.30chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_TM_and_ETMplus.img:  21%|██        | 7/

[INFO] Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img as ENVI_band_
[INFO] Processing raster: YELL_2023_07_C/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance/NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img with 5 bands.



Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img:   0%|          | 0/34 [00:00<?, ?chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img:   6%|▌         | 2/34 [00:00<00:02, 11.33chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img:  12%|█▏        | 4/34 [00:00<00:03,  8.05chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img:  15%|█▍        | 5/34 [00:00<00:04,  7.17chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img:  18%|█▊        | 6/34 [00:00<00:04,  6.08chunk/s]
Processing NEON_D12_YELL_DP1_L001-1_20230711_directional_reflectance__envi_resample_MicaSense-to-match_OLI_and_OLI-2.img:  21%|██        | 7/34 [00

Jefe finished. Please check for the _with_mask_and_all_spectra.csv for your  hyperspectral data from NEON flight lines extracted to match your provided polygons


In [ ]:
# YELL - 2023-07 (Part 2)
base_folder = 'YELL_2023_07'
site_code = 'YELL'
product_code = 'DP1.30006.001'
year_month = '2023-07'
flight_lines = [
    'NEON_D12_YELL_DP1_L033-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L036-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L037-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L038-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L040-1_20230715_directional_reflectance',
    'NEON_D12_YELL_DP1_L046-1_20230703_directional_reflectance',
    'NEON_D12_YELL_DP1_L050-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L051-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L065-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L067-1_20230712_directional_reflectance',
    'NEON_D12_YELL_DP1_L073-1_20230719_directional_reflectance',
    'NEON_D12_YELL_DP1_L074-1_20230718_directional_reflectance',
    'NEON_D12_YELL_DP1_L075-1_20230718_directional_reflectance'
]
el_spectral.jefe(base_folder, site_code, product_code, year_month, flight_lines)

Processing flight line: NEON_D12_YELL_DP1_L033-1_20230715_directional_reflectance
Data retrieved successfully for 2023-07!
Download completed for NEON_D12_YELL_DP1_L033-1_20230715_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D12_YELL_DP1_L036-1_20230715_directional_reflectance
Data retrieved successfully for 2023-07!
Download completed for NEON_D12_YELL_DP1_L036-1_20230715_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D12_YELL_DP1_L037-1_20230715_directional_reflectance
Data retrieved successfully for 2023-07!
Download completed for NEON_D12_YELL_DP1_L037-1_20230715_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D12_YELL_DP1_L038-1_20230715_directional_reflectance
Data retrieved successfully for 2023-07!
Download completed for NEON_D12_YELL_DP1_L038-1_20230715_directional_reflectance.h5
Download completed.

Processing flight line: NEON_D12_YELL_DP1_L040-1_20230715_directional_reflectance
Data r

In [78]:
import pandas as pd

# Path to the cleaned CSV file
cleaned_csv = "next_test/NEON_D13_NIWO_DP1_20200731_155646_reflectance/NEON_D13_NIWO_DP1_20200731_155646_reflectance__envi_masked_spectral_data.csv"

# Load the first few rows of the cleaned CSV file
df_preview = pd.read_csv(cleaned_csv, nrows=50)

# Display all columns in the preview
pd.set_option('display.max_columns', None)  # Show all columns
print(df_preview)

    CreationDate  Creator  EditDate  Editor  GlobalID  OBJECTID  \
0            NaN      NaN       NaN     NaN       NaN       NaN   
1            NaN      NaN       NaN     NaN       NaN       NaN   
2            NaN      NaN       NaN     NaN       NaN       NaN   
3            NaN      NaN       NaN     NaN       NaN       NaN   
4            NaN      NaN       NaN     NaN       NaN       NaN   
5            NaN      NaN       NaN     NaN       NaN       NaN   
6            NaN      NaN       NaN     NaN       NaN       NaN   
7            NaN      NaN       NaN     NaN       NaN       NaN   
8            NaN      NaN       NaN     NaN       NaN       NaN   
9            NaN      NaN       NaN     NaN       NaN       NaN   
10           NaN      NaN       NaN     NaN       NaN       NaN   
11           NaN      NaN       NaN     NaN       NaN       NaN   
12           NaN      NaN       NaN     NaN       NaN       NaN   
13           NaN      NaN       NaN     NaN       NaN       Na